In [2]:
import copy
import json
import os

from collections import Counter, defaultdict
from itertools import chain

from IPython.display import display, IFrame

In [3]:
TIGER = 'tiger_2.2_JSON/'
OUT_DIR = 'tiger_2.2_UD_headed_JSON'

tree_jsons = []

for jsonfile in sorted(os.listdir(TIGER)):
    with open(os.path.join(TIGER, jsonfile)) as f:
        tree_jsons.append(json.load(f))
        if len(tree_jsons) % 1000 == 0:
            print(len(tree_jsons))

len(tree_jsons)

1000
2000
3000
4000
5000
6000
7000
8000
9000
10000
11000
12000
13000
14000
15000
16000
17000
18000
19000
20000
21000
22000
23000
24000
25000
26000
27000
28000
29000
30000
31000
32000
33000
34000
35000
36000
37000
38000
39000
40000
41000
42000
43000
44000
45000
46000
47000
48000
49000
50000


50472

In [4]:
tree_jsons[0]

{'metadata': {'sent_id': 's1',
  'corp_id': 'Tiger2.2',
  'text_id': '0001_0001',
  'split': 'train',
  'tiger_src': 'Frankfurter Rundschau 199207?? ??? ?????????',
  'tiger_elem': 'Header',
  'text': "`` Ross Perot wäre vielleicht ein prächtiger Diktator ''"},
 'tree': {'category': 'VROOT',
  'is_head': True,
  'span': {'from': 0, 'to': 9},
  'attributes': {'id': 's1_VROOT'},
  'children': [{'is_head': False,
    'span': {'from': 0, 'to': 1},
    'orth': '``',
    'base': '--',
    'tag': '$(:--',
    'features': {'id': 's1_1', 'pos': '$(', 'morph': '--', 'disamb': 'true'},
    'deprel': '--'},
   {'category': 'S',
    'is_head': False,
    'span': {'from': 1, 'to': 8},
    'attributes': {'id': 's1_502'},
    'children': [{'category': 'PN',
      'is_head': False,
      'span': {'from': 1, 'to': 3},
      'attributes': {'id': 's1_500'},
      'children': [{'is_head': False,
        'span': {'from': 1, 'to': 2},
        'orth': 'Ross',
        'base': 'Ross',
        'tag': 'NE:Nom:Sg:

In [5]:
TIGER_UD = 'tiger_release_aug07.corrected.16012013.conll09'

In [6]:
import conllu

with open(TIGER_UD) as f:
    tiger_ud = conllu.parse_incr(
        f,
        fields=['id', 'form', 'lemma', 'f1','xpos', 'f2', 'feats', 'f3', 'head', 'f4', 'deprel'],
        field_parsers={'id' : lambda line, i: line[i].split('_')[1]}
    )
    tiger_ud = list(tiger_ud)

In [7]:
tiger_ud[0]

TokenList<``, Ross, Perot, wäre, vielleicht, ein, prächtiger, Diktator, ''>

In [8]:
len(tree_jsons), len(tiger_ud)

(50472, 50472)

In [9]:
tiger_ud[0][0]

{'id': '1',
 'form': '``',
 'lemma': '--',
 'f1': '_',
 'xpos': '$(',
 'f2': '_',
 'feats': None,
 'f3': '_',
 'head': 4,
 'f4': '_',
 'deprel': '--'}

In [10]:
import urllib.parse

def show_tree(tree_json):
    tree_json = json.dumps(tree_json)
    src = f'http://127.0.0.1:8010/?tree={urllib.parse.quote(tree_json)}'
    display(IFrame(src, 950, 550))

def show_json(tree_json):
    show_tree(tree_json['tree'])

In [11]:
from spacy import displacy

def to_deps(conllu):
    deps = {'words' : [], 'arcs' : []}
    for token in conllu:
        idx = int(token['id'])
        deps['words'].append({'text' : token['form'], 'tag' : token['xpos']})
        if token['head'] > 0:
            d = 'left' if token['head'] > idx else 'right'
            start, end = sorted((idx, token['head']))
            deps['arcs'].append({'start' : start - 1, 'end' : end - 1, 'label' : token['deprel'], 'dir' : d})
    return deps

def display_deps(conllu):    displacy.render(to_deps(conllu), manual=True, options={'distance' : 80})

In [12]:
def get_yield(tree):
    if 'children' not in tree:
        return [tree]
    else:
        yld = []
        for child in tree['children']:
            yld += get_yield(child)
        return yld

def tree_from_ud_tokens(ud_tokens):
    tokens = [{'id' : 0, 'deprel': '<ROOT>', 'form': '<ROOT>', 'children' : []}]
    tokens += [
        {
            'id' : int(token['id']),
            'deprel': token['deprel'],
            'form': token['form'],
            'xpos': token['xpos'],
            'children' : []
        }
        for token in ud_tokens
    ]
    for token in ud_tokens:
        tokens[token['head']]['children'].append(tokens[int(token['id'])])
    return tokens[0]

def _collect_headed_spans(ud_tree, spans):
    my_span = [(ud_tree['id'] - 1, ud_tree['form'])]
    for child in ud_tree['children']:
        child_span = _collect_headed_spans(child, spans)
        my_span += child_span
        spans.append([ud_tree['id'], tuple(child_span)])
    my_span = sorted(my_span)
    return my_span

def collect_headed_spans(ud_tree):
    spans = []
    _collect_headed_spans(ud_tree, spans)
    span2head = {}
    for idx, span in spans:
        span2head[span] = idx - 1
    return span2head

def get_head2span(ud_tree):
    head2span = defaultdict(set)
    for span, head in collect_headed_spans(ud_tree).items():
        head2span[head].add(head)
        head2span[head].update([idx for idx, token in span])
    return {head : tuple(sorted(span)) for head, span in head2span.items()}

'''
def is_dependency_head(span1, span2, span2head):
    #print('---------------------------')
    #print('is', span1, 'the head of', span2, '?')
    idx1 = [idx for idx, form in span1]
    for span, head in span2head.items():
        #print('   ', span, '<===', head)
        if set(span2).issubset(span) and head in idx1:
            return True 
    return False
''';

In [13]:
def is_punctuation(tiger_tree):
    if 'children' in tiger_tree:
        return False
    elif tiger_tree['tag'] in ['$(:--', '$,:--', '$.:--']:
        return True
    return False

def collect_node_spans(tiger_tree, spans, ignore_punct=False, include_terminals=False):
    if 'children' not in tiger_tree:
        if ignore_punct and is_punctuation(tiger_tree):
            return []
        else:
            my_span = [tiger_tree['span']['from']]
            if include_terminals:
                spans.append([tiger_tree, my_span])
            return my_span
    else:
        my_span = []
        for child in tiger_tree['children']:
            my_span += collect_node_spans(child, spans, ignore_punct=ignore_punct, include_terminals=include_terminals)
        my_span = sorted(my_span)
        spans.append([tiger_tree, my_span])
        return my_span

def _remove_punct(tiger_json):
    removed = []
    if 'children' in tiger_json:
        new_children = []
        for child in tiger_json['children']:
            removed += _remove_punct(child)
            if not is_punctuation(child):
                new_children.append(child)
            else:
                removed.append((child, tiger_json['attributes']['id']))
        tiger_json['children'] = new_children
    return removed

def remove_punct(tiger_tree):
    new_tree = copy.deepcopy(tiger_tree)
    removed = _remove_punct(new_tree)
    return new_tree, removed

def is_punctuation_ud(ud_tree):
    if ud_tree['children']:
        return False
    if ud_tree['xpos'] in ['$(', '$,', '$.']:
        return True
    return False

def _remove_punct_ud(ud_tree):
    if 'children' in ud_tree:
        new_children = []
        for child in ud_tree['children']:
            _remove_punct_ud(child)
            if not is_punctuation_ud(child):
                new_children.append(child)
        ud_tree['children'] = new_children

def remove_punct_ud(ud_tree):
    new_tree = copy.deepcopy(ud_tree)
    _remove_punct_ud(new_tree)
    return new_tree

def choose_lowest(nodes):
    lowest = []
    for n1 in nodes:
        is_parent = False
        for n2 in nodes:
            if n2 in n1['children']:
                is_parent = True
        if not is_parent:
            lowest.append(n1)
    return lowest

def reattach_punctuation(tiger_tree, ud_tokens):
    no_punct_tiger_tree, punct = remove_punct(tiger_tree)
    if punct:
        ud_tree = tree_from_ud_tokens(ud_tokens)
        no_punct_ud_tree = remove_punct_ud(ud_tree)
        head2span = get_head2span(no_punct_ud_tree)
        
        tiger_spans = []
        collect_node_spans(no_punct_tiger_tree, tiger_spans, include_terminals=True)
        
        tiger_span2node = defaultdict(list)
        id2span, id2node = dict(), dict()
        for node, span in tiger_spans:
            tiger_span2node[tuple(sorted(span))].append(node)
            node_idx = node['attributes' if 'attributes' in node else 'features']['id']
            id2span[node_idx] = tuple(sorted(span))
            id2node[node_idx] = node
        
        reattach = False
        for p, parent_id in punct:
            tiger_parent_span = id2span[parent_id]
            idx = p['span']['from']
            head_idx = ud_tokens[idx]['head'] - 1
            try:
                ud_head_span = head2span.get(head_idx, (head_idx,))
            except:
                print(idx, ud_tokens[idx])
                print(head_idx, ud_tokens[head_idx])
                display(head2span)
                raise
            if tiger_parent_span == ud_head_span:
                id2node[parent_id]['children'].append(p)
            else:
                reattach = True
                #print(p)
                #print('    TIGER PARENT SPAN:', tiger_parent_span)
                #print('    UD HEAD SPAN     :', ud_head_span)
                new_parent_candidates = tiger_span2node[ud_head_span]
                if len(new_parent_candidates) > 1:
                    new_parent_candidates = choose_lowest(new_parent_candidates)
                try:
                    assert(len(new_parent_candidates) == 1)
                except:
                    print('*********************************')
                    show_tree(tiger_tree)
                    show_tree(no_punct_tiger_tree)
                    print('*********************************')
                    print('CANDIDATE PARENTS FOR:', p)
                    print('UD HEAD SPAN:', ud_head_span)
                    for node in new_parent_candidates:
                        print('NODE:', node['category'])
                    print('TIGER SPANS:')
                    for node, span in tiger_spans:
                        print('   ***', node['category'] if 'category' in node else 'TERMINAL')
                        print('   ******', span)
                    
                    for span, nodes in tiger_span2node.items():
                        print(span)
                        for node in nodes:
                            print('   ===', node['category'] if 'category' in node else 'TERMINAL')
                    raise
                new_parent = new_parent_candidates[0]
                #print('        reattach to:')
                #print('         ->', new_parent['category'])
                if 'children' not in new_parent:
                    # terminal -> node
                    terminal = copy.deepcopy(new_parent)
                    new_parent.pop('orth')
                    new_parent.pop('base')
                    new_parent.pop('tag')
                    new_parent['category'] = 'DUMMY'
                    new_parent['attributes'] = {'id': f'pre_{terminal["features"]["id"]}'}
                    new_parent['children'] = [terminal]
                    terminal['is_head'] = True
                    terminal['deprel'] = 'HD'
                    #print(new_parent)
                new_parent['children'].append(p)
        #if reattach:
        #    show_tree(tiger_tree)
        #    show_tree(no_punct_tiger_tree)
        #    display_deps(ud_tokens)
    
        return no_punct_tiger_tree, reattach
    
    else:
        return tiger_tree, False

In [14]:
COORDINATION = ('CS', 'CVP', 'CVZ', 'CCP', 'CNP', 'CPP', 'CAP', 'CAVP', 'CAC', 'CO',)

In [15]:
def find_smallest_superset(span, spans):
    candidates = [s for s in spans if set(s).issuperset(span) and s != span]
    candidates = sorted(candidates, key=lambda x: len(x))
    #print('CANDIDATES:', candidates)
    return candidates[0]

def introduce_phrase(parent, new_category, new_span):
    #show_tree(parent)
    new_children, new_node_children = [], []
    new_from, new_to = new_span[0], new_span[-1]
    #print(new_from, new_to)
    for child in parent['children']:
        child_span = set(leaf['span']['from'] for leaf in get_yield(child))
        if child_span.issubset(new_span):
            #print('-> APPEND TO NEW NODE')
            new_node_children.append(child)
        else:
            #print('-> KEEP OLD PARENT')
            new_children.append(child)
    new_node = {
        'category' : new_category,
        'is_head' : False,
        'span': {'from': new_from, 'to': new_to},
        'attributes': {'id': f'new_{new_category}'},
        'children' : new_node_children,
    }
    new_children.append(new_node)
    parent['children'] = new_children
    #show_tree(parent)

def introduce_missing_phrases(tiger_tree, ud_tokens):
    ud_tree = tree_from_ud_tokens(ud_tokens)
    no_punct_ud_tree = remove_punct_ud(ud_tree)
    tiger_spans = []
    collect_node_spans(tiger_tree, tiger_spans, ignore_punct=True)
    head2span = get_head2span(no_punct_ud_tree)
    
    _tiger_spans = set(tuple(span) for node, span in tiger_spans)
    _ud_spans = set(tuple(filter(lambda x: x != -1, span)) for span in head2span.values())
    
    tiger_span2node = defaultdict(list)
    #id2span, id2node = dict(), dict()
    for node, span in tiger_spans:
        tiger_span2node[tuple(sorted(span))].append(node)
        #id2span[node['attributes']['id']] = tuple(sorted(span))
        #id2node[node['attributes']['id']] = node
    
    for _ud_span in _ud_spans:
        if _ud_span not in _tiger_spans:
            #print('========>', _ud_span)
            parent_span = find_smallest_superset(_ud_span, _tiger_spans)
            #print('PARENT:', parent_span)
            parent_nodes = [node for node in tiger_span2node[parent_span] if node['category'] != 'VROOT']
            if len(parent_nodes) > 1:
                parent_nodes = choose_lowest(parent_nodes)
            try:
                assert(len(parent_nodes) == 1)
            except:
                print('SPAN', [ud_tokens[i]['form'] for i in _ud_span])
                print('PARENT CANDIDATES:')
                display(parent_nodes)
                raise
            parent_node = parent_nodes[0]
            # coordination is handled differently
            if parent_node['category'] in COORDINATION:
                continue
            try:
                assert(parent_node['category'] == 'PP')
            except:
                show_tree(tiger_tree)
                print('PARENT:', parent_node['category'])
                print('SPAN', [ud_tokens[i]['form'] for i in _ud_span])
                raise
            introduce_phrase(parent_node, 'NP', _ud_span)

In [16]:
PERIOD = []

def _preprocess(node):
    if 'children' not in node:
        return
    # clear any head markings
    for child in node['children']:
        child['is_head'] = False
        _preprocess(child)

def preprocess(tree_json):
    copied = copy.deepcopy(tree_json)
    _preprocess(copied['tree'])
    # change final punctuation to special tags
    if 'children' in copied['tree']:
        for child in sorted(copied['tree']['children'], key=lambda x: -x['span']['to']):
            if 'children' not in child and child['features']['pos'] in PERIOD:
                child['tag'] = 'PERIOD:--'
            else:
                break
    return copied

def preprocess_ud(ud_tokens):
    # change final punctuation to special tags
    root_idx = [i + 1 for i, token in enumerate(ud_tokens) if token['head'] == 0]
    assert(len(root_idx) == 1)
    root_idx = root_idx[0]
    for token in reversed(ud_tokens):
        if token['xpos'] in PERIOD and token['head'] == root_idx:
            token['xpos'] = 'PERIOD'
        else:
            break

In [17]:
def get_id(node):
    if 'attributes' in node:
        return node['attributes']['id']
    else:
        return node['features']['id']

def id2parent(tiger_tree):
    ret = dict()
    for child in tiger_tree.get('children', []):
        ret.update(id2parent(child))
        ret[get_id(child)] = tiger_tree
    return ret

def _node_covers_span(node, left, right):
    node_span = [leaf['span']['from'] for leaf in get_yield(node)]
    return left in node_span and right in node_span

def _lowest_covering_node(tiger_tree, left, right, tab=''):
    #print(tab, tiger_tree.get('category', 'TERMINAL'), tiger_tree['span'], left, right)
    if _node_covers_span(tiger_tree, left, right):
        for child in tiger_tree.get('children', []):
            lcn = _lowest_covering_node(child, left, right, tab=tab + '  ')
            if lcn:
                return lcn
        return tiger_tree
    else:
        return None

def lowest_common_ancestor(tiger_tree, left, right):
    _left = left['span']['from']
    _right = right['span']['from']
    return _lowest_covering_node(tiger_tree, _left, _right)

CLOSING = {
    '``' : "''",
    '(' : ')',
    '`' : "'",
}

DUMMY_CAT = 'NODE'

def reattach_node(node, parents, new_parent):
    old_parent = parents[get_id(node)]
    #print('\nREATTACHING:', node)
    #print('OLD PARENT:', old_parent['category'], old_parent['span'])
    #print('NEW PARENT:', new_parent.get('category', 'TERMINAL'), new_parent['span'])
    old_parent['children'].remove(node)
    
    if 'children' not in new_parent:
        # terminal -> node
        terminal = copy.deepcopy(new_parent)
        new_parent.pop('orth')
        new_parent.pop('base')
        new_parent.pop('tag')
        new_parent['category'] = DUMMY_CAT
        new_parent['attributes'] = {'id': f'pre_{terminal["features"]["id"]}'}
        new_parent['children'] = [terminal]
        terminal['is_head'] = True
        terminal['deprel'] = 'HD'
    
    new_parent['children'].append(node)
    new_parent['children'] = sorted(new_parent['children'], key=lambda x: x['span']['from'])
    parents[get_id(node)] = new_parent

def reattach_punctuation2(tiger_tree):
    #show_tree(tiger_tree)
    reattached = False
    leaves = sorted(get_yield(tiger_tree), key=lambda x: x['span']['from'])
    punct = [leaf for leaf in leaves if leaf['features']['pos'][0] == '$']
    parents = id2parent(tiger_tree)
    for leaf in punct:
        leaf_idx = leaf['span']['from']
        leaf_id = get_id(leaf)
        # recalculate leaves (may have changed if NODE was introduced)
        leaves = sorted(get_yield(tiger_tree), key=lambda x: x['span']['from'])
        # for enclosing punctuation try to find the corresponding symbol and attach them to the node
        # that covers the span within
        if leaf['features']['pos'] == '$(' and leaf['orth'] in ('``', '(', '`'):
            #print(leaf)
            #print(leaf_idx)
            closing = [l for l in leaves[(leaf_idx + 1):] if l['orth'] == CLOSING[leaf['orth']]]
            if closing:
                #display(closing)
                closing = closing[0]
                closing_idx = closing['span']['from']
                #display(leaves[(leaf_idx + 1):closing_idx])
                words_between = [l for l in leaves[(leaf_idx + 1):closing_idx] if l['features']['pos'][0] != '$']
                if words_between:
                    left, right = words_between[0], words_between[-1]
                    new_parent = lowest_common_ancestor(tiger_tree, left, right)
                    reattach_node(leaf, parents, new_parent)
                    reattach_node(closing, parents, new_parent)
                    reattached = True
        # try to reattach from root to the deepest common ancestor of the left and the right neighbor
        elif parents[leaf_id] == tiger_tree:
            words_before = [l for l in leaves[:leaf_idx] if l['features']['pos'][0] != '$']
            words_after = [l for l in leaves[(leaf_idx + 1):] if l['features']['pos'][0] != '$']
            before = words_before[-1] if words_before else None
            after = words_after[0] if words_after else None
            # don't do anything to one word sentences (this should never happen)
            if not before and not after:
                1/0
            # leave punct at the root if it is the first/last token
            elif not before or not after:
                pass
            else:
                new_parent = lowest_common_ancestor(tiger_tree, before, after)
                reattach_node(leaf, parents, new_parent)
                reattached = True
    #if reattached:
    #    show_tree(tiger_tree)
    return reattached

In [29]:
def _mark_heads(tiger_tree, span2head):
    if 'children' not in tiger_tree:
        #print('======', tiger_tree['span']['from'], tiger_tree['orth'])
        if is_punctuation(tiger_tree):
            return ()
        if True:
            idx = tiger_tree['span']['from']
            return ((idx, tiger_tree['orth']),)
    my_span, child_spans = [], []
    for child in tiger_tree['children']:
        child_span = _mark_heads(child, span2head)
        my_span += child_span
        child_spans.append(child_span)
    my_span = tuple(sorted(my_span))
    if len(tiger_tree['children']) == 1:
        tiger_tree['children'][0]['is_head'] = True
        return my_span
    # head already marked when the dummy node was created
    if tiger_tree['category'] == DUMMY_CAT:
        return my_span
    
    #print('CAT:', tiger_tree['category'], 'SPAN:', my_span)
    head_candidates = []
    for child, child_span in zip(tiger_tree['children'], child_spans):
        if is_punctuation(child):
            continue
        #print('    CHILD:', child_span)
        child_dependency_head = span2head.get(child_span, None)
        #print('    CHILD DEP HEAD:', child_dependency_head)
        if child_dependency_head is None or child_dependency_head == -1:
            head_candidates.append([child, child_span])
    '''if len(head_candidates) == 2 and tiger_tree['category'] == 'PP':
        hd1, hd2 = head_candidates
        #print('HD1:', hd1[0])
        #print('HD2:', hd2[0])
        head12 = is_dependency_head(hd1[1], hd2[1], span2head)
        head21 = is_dependency_head(hd2[1], hd1[1], span2head)
        if head12:
            assert(not head21)
            PP_head, NP_head = hd1[0], hd2[0]
        elif head21:
            PP_head, NP_head = hd2[0], hd1[0]
        else:
            print('**********', head12, head21)
            1/0
        PP_children, NP_children = [], []
        for child in tiger_tree['children']:
            if child != PP_head and child != NP_head:
                # from https://www.ims.uni-stuttgart.de/forschung/ressourcen/werkzeuge/tiger2dep/
                if child['deprel'] not in ['AC', 'PH', 'MO', 'CM']:
                    NP_children.append(child)
                else:
                    PP_children.append(child)
        PP_head['is_head'] = True
        NP_head['is_head'] = True
        new_NP_children = [NP_head] + NP_children
        new_NP_from = min(ch['span']['from'] for ch in new_NP_children)
        new_NP_to = min(ch['span']['to'] for ch in new_NP_children)
        new_NP = {
            'category' : 'NP',
            'is_head' : False,
            'span': {'from': new_NP_from, 'to': new_NP_to},
            'attributes': {'id': 'new_NP'},
            'children' : new_NP_children,
        }
        tiger_tree['children'] = [PP_head] + PP_children + [new_NP]
    ''';
    #if len(head_candidates) > 1 and tiger_tree['category'] in COORDINATION:
    if tiger_tree['category'] in COORDINATION:
        head_candidates = []
        conjunctions = [c for c in tiger_tree['children'] if c['deprel'] == 'CD']
        commas = [c for c in tiger_tree['children'] if is_punctuation(c) and c['tag'] == '$,:--']
        conjuncts = [c for c in tiger_tree['children'] if c['deprel'] == 'CJ']
        if conjunctions:
            conjunctions[0]['is_head'] = True
        elif commas:
            commas[0]['is_head'] = True
        elif conjuncts:
            conjuncts[0]['is_head'] = True
        else:
            print('###################', tiger_tree['category'], my_span)
            1/0
    else:
        try:
            assert(len(head_candidates) == 1)
        except:
            print('!!!!!!!!!!!!', tiger_tree['category'], my_span)
            for node, span in head_candidates:
                print('=======', node.get('category', 'TERMINAL'), span)
            raise
        head_candidates[0][0]['is_head'] = True
    
    # for introduced NPs
    if 'deprel' not in tiger_tree:
        assert(tiger_tree['category'] == 'NP')
        tiger_tree['deprel'] = head_candidates[0][0]['deprel']
    
    return my_span

#        nphead = self.__find_head(sentence,rootid,daughters,'NP')
#        if nphead:
#            for d in [ d for d in daughters if d.label not in ['AC','PH','MO','CM'] and d.nid != nphead.nid ]:
#                sentence[d.nid-1].head = nphead.nid

def mark_heads(tiger_json, ud_tokens):
    ud_tokens = copy.deepcopy(ud_tokens)
    ud_tree = tree_from_ud_tokens(ud_tokens)
    ud_tree_no_punct = remove_punct_ud(ud_tree)
    #span2head = collect_headed_spans(ud_tree)
    span2head = collect_headed_spans(ud_tree_no_punct)
    new_json = copy.deepcopy(tiger_json)
    #spans = []
    
    #collect_node_spans(tiger_tree, spans)
    
    tiger_tree = new_json['tree']
    
    introduce_missing_phrases(tiger_tree, ud_tokens)
    
    #print('=======================')
    #show_tree(tiger_tree)
    #punct_tree, changed = reattach_punctuation(tiger_tree, ud_tokens)
    changed = reattach_punctuation2(tiger_tree)
    #show_tree(tiger_tree)
    try:
        _mark_heads(tiger_tree, span2head)
    except:
        #show_tree(tiger_tree)
        #display(span2head)
        raise
    return {'metadata' : tiger_json['metadata'], 'tree' : tiger_tree}, changed

PROCESSED_JSONS = []

SKIP = (
    #'s879', # `` an den Verhandlungstisch '' -> cudzysłowy w UD do <den Verhandlungstisch>;
            # prawdopodobnie błąd przy przepinaniu podrzędników przy tworzeniu PP
    's365', # analogicznie: `` In Maschhad ''
    's46234', # Faune Faune, Nymphen Nymphen
    's50224', # podobnie
)

SKIP_XPOS = [
    ['APPRART', 'NN', '$.'],
    ['APPR', 'NN', '$.'],
    ['APPR', 'NN', '$('],
    ['APPRART', 'ADJA', '$.'],
    ['APPR', 'ADV', '$.'],
    ['APPR', '$.', 'NN'],
]

M, N = 0, 1000000
i = M

SKIPPED = Counter()

for tiger_json, ud_tokens in zip(tree_jsons[M:N], tiger_ud[M:N]):
    i += 1
    
    ud_tokens = copy.deepcopy(ud_tokens)
    
    if tiger_json['metadata']['tiger_elem'] == 'Meta':
        SKIPPED['Meta'] += 1
        continue
    
    if tiger_json['metadata']['sent_id'] in SKIP:
        SKIPPED['list 1'] += 1
        continue
    
    if len(ud_tokens) == 1:
        SKIPPED['len 1'] += 1
        continue
    
    if [token['xpos'] for token in ud_tokens] in SKIP_XPOS:
        SKIPPED['list 2'] += 1
        continue
    
    # some trees have multiple roots!
    roots = [token for token in ud_tokens if token['head'] == 0]
    if len(roots) != 1:
        # if there is only one ‘proper word’ root, choose it
        r1, r2 = [], []
        for root in roots:
            if root['xpos'][0] == '$' or root['xpos'] == 'XY':
                r2.append(root)
            else:
                r1.append(root)
        # if there is only one ‘proper word’ root, choose it
        if len(r1) == 1:
            root_idx = int(r1[0]['id'])
            for root in r2:
                root['head'] = root_idx
        # if there is only one ‘punctuation’ root, choose it
        #elif len(r2) == 1 and r2[0]['xpos'][0] == '$':
        #    root_idx = int(r2[0]['id'])
        #    for root in r1:
        #        root['head'] = root_idx
        else:
            #if tiger_json['metadata']['tiger_elem'] != 'Meta':
            #    show_json(tiger_json)
            #    print(tiger_json['metadata'])
            #    display_deps(ud_tokens)
            #    for root in roots:
            #        print(root['id'], root['form'], root['xpos'], root['head'])
            SKIPPED[f'multiple roots ({tiger_json["metadata"]["tiger_elem"]})'] += 1
            continue
    
    #if len(ud_tokens) > 16:
    #    continue
    
    #show_json(tiger_json)
    #display_deps(ud_tokens)
    preprocess_ud(ud_tokens)
    
    tiger_json = preprocess(tiger_json)
    tiger_tree = tiger_json['tree']
    tokens1 = [leaf['orth'] for leaf in sorted(get_yield(tiger_tree), key=lambda x: x['span']['from'])]
    tokens2 = [token['form'] for token in ud_tokens]
    try:
        assert(tokens1 == tokens2)
    except:
        print(tokens1)
        print(tokens2)
        print(tiger_json['metadata'])
        raise
    try:
        headed_tiger_json, changed = mark_heads(tiger_json, ud_tokens)
        #show_json(headed_tiger_json)
        #if changed:
        #    show_json(tiger_json)
        #    display_deps(ud_tokens)
        #    show_json(headed_tiger_json)
        PROCESSED_JSONS.append(headed_tiger_json)
    except:
        print('=================', i - 1)
        display_deps(ud_tokens)
        show_json(tiger_json)
        #show_tree(headed_tiger_json)
        print(tiger_json['metadata'])
        SKIPPED['error'] += 1
        #raise

!!!!!!!!!!!! S ((0, 'Dazu'), (1, 'Krause'))
================= 1007


{'sent_id': 's1008', 'corp_id': 'Tiger2.2', 'text_id': '0001_0033', 'split': 'train', 'tiger_src': 'Frankfurter Rundschau 199207?? ??? ?????????', 'tiger_elem': 'Body', 'text': 'Dazu Krause : `` Ich vertrete meine Region mit ihren Problemen im Bundestag genauso , wie es auch West-Kollegen tun .'}
!!!!!!!!!!!! S ((22, 'vor'), (23, 'sich'), (24, 'das'), (25, 'Mikrofon'), (26, 'und'), (27, 'eine'), (28, 'Belegschaft'), (30, 'die'), (31, 'Angst'), (32, 'vor'), (33, 'morgen'), (34, 'hat'))
================= 1808


{'sent_id': 's1809', 'corp_id': 'Tiger2.2', 'text_id': '0001_0094', 'split': 'train', 'tiger_src': 'Frankfurter Rundschau 199207?? ??? ?????????', 'tiger_authors': 'Peter Ziller|masc', 'tiger_elem': 'Body', 'text': "Hinter sich die Transparente `` Stopp der Arbeitsplatzvernichtung '' und `` Wir haben nichts mehr zu verlieren außer unseren Arbeitsplätzen '' , vor sich das Mikrofon und eine Belegschaft , die Angst vor morgen hat ."}
!!!!!!!!!!!! S ((10, 'Fachpersonal'), (11, 'bereitgestellt'))
================= 3261


{'sent_id': 's3262', 'corp_id': 'Tiger2.2', 'text_id': '0001_0184', 'split': 'dev', 'tiger_src': 'Frankfurter Rundschau 199207?? ??? ?????????', 'tiger_elem': 'Body', 'text': 'Das sei möglich , wenn - kurzfristig Ausrüstungslieferungen erhöht , Fachpersonal bereitgestellt und Know-how transferiert sowie - mittel- und langfristig die Exploration und Entwicklung von Öl- und Gasfeldern beschleunigt würden .'}
!!!!!!!!!!!! S ((28, 'Schwarzenberger'), (29, 'mit'), (30, 'Fesseln'))
================= 7266


{'sent_id': 's7267', 'corp_id': 'Tiger2.2', 'text_id': '0150_0001', 'split': 'train', 'tiger_src': 'Frankfurter Rundschau 19951107 FEU D10300734', 'tiger_authors': 'Robert Fischer|masc', 'tiger_elem': 'Body', 'text': 'Alle drei Regisseure waren auch in diesem Jahr mit neuen Filmen in Hof vertreten : Rödl mit Ein Richter in Angst , Graf mit Frau Bu lacht , Schwarzenberger mit Fesseln .'}
!!!!!!!!!!!! S ((9, 'Nach'), (10, 'fünf'), (11, 'im'), (12, 'Urwald'))
================= 7289


...

{'sent_id': 's47835', 'corp_id': 'Tiger2.2', 'text_id': '2155_0001', 'split': 'train', 'tiger_src': 'Frankfurter Rundschau 19970215 POL D02030478', 'tiger_authors': 'Stephan Hebel|masc', 'tiger_elem': 'Body', 'text': "Diesmal reist er die Lahn herauf und herunter , drei Tage lang : Erst Koblenz , dann Bad Ems ( `` ich habe mich auf der Hinfahrt erkundigt , wo das überhaupt liegt '' ) , jetzt wieder Koblenz ."}
!!!!!!!!!!!! S ((19, 'zwischen'), (20, 'den'), (21, 'Augenbrauen'), (22, 'eine'), (23, 'feine'), (25, 'sensible'), (26, 'Falte'))
================= 48410


{'sent_id': 's48413', 'corp_id': 'Tiger2.2', 'text_id': '2163_0001', 'split': 'train', 'tiger_src': 'Frankfurter Rundschau 19970215 MRE D02091075', 'tiger_authors': 'Nora Sobich|fem', 'tiger_elem': 'Body', 'text': 'Der Gesichtsausdruck ist streng , die Nase gerade und groß , die Haare von hinten nach vorn gekämmt , zwischen den Augenbrauen eine feine , sensible Falte .'}
!!!!!!!!!!!! S ((27, 'darüber'), (28, 'die'), (29, 'lineare'), (30, 'Großform'), (31, 'der'), (32, 'zeichenhaft'), (33, 'vereinfachten'), (34, 'Staffelei'), (36, 'die'), (37, 'in'), (38, 'den'), (39, 'nachfolgenden'), (40, 'Bildern'), (41, 'als'), (42, 'Leitmotiv'), (43, 'immer'), (44, 'wieder'), (45, 'auftaucht'))
================= 48856


{'sent_id': 's48859', 'corp_id': 'Tiger2.2', 'text_id': '2172_0001', 'split': 'train', 'tiger_src': 'Frankfurter Rundschau 19970215 FEU D02140013', 'tiger_authors': 'Gabriele Hoffmann|fem', 'tiger_elem': 'Body', 'text': 'Auf einem Tisch ein Arrangement flächig miteinander verspannter Gegenstände - Palette und Pinsel , eine Orange auf einem Teller , ein Glas , eine Blattpflanze - und darüber die lineare Großform der zeichenhaft vereinfachten Staffelei , die in den nachfolgenden Bildern als Leitmotiv immer wieder auftaucht .'}
!!!!!!!!!!!! S ((19, 'Temperatur'), (21, 'zehn'), (22, 'Grad'), (23, 'minus'))
================= 50240


{'sent_id': 's50243', 'corp_id': 'Tiger2.2', 'text_id': '2249_0001', 'split': 'train', 'tiger_src': 'Frankfurter Rundschau 19970311 DOK D02180654', 'tiger_authors': 'Hannelore Jaresch|fem', 'tiger_elem': 'Body', 'text': 'Die Wagen sind älterer Bauart , die Seitenöffnungen nur notdürftig auf einer Seite mit einer schmalen Plane verschlossen ( Temperatur : zehn Grad minus ) .'}
!!!!!!!!!!!! S ((24, 'einige'), (25, 'auf'), (26, 'einem'), (27, 'Auge'), (28, 'oder'), (29, 'sogar'), (30, 'beidseitig'), (31, 'blind'))
================= 50246


{'sent_id': 's50249', 'corp_id': 'Tiger2.2', 'text_id': '2249_0001', 'split': 'train', 'tiger_src': 'Frankfurter Rundschau 19970311 DOK D02180654', 'tiger_authors': 'Hannelore Jaresch|fem', 'tiger_elem': 'Body', 'text': 'Es sind zum großen Teil ausgediente Pferde aus der polnischen Landwirtschaft , zum Teil stark lahmend , mit erschreckenden Hufdeformationen , eingefallenen Rücken , einige auf einem Auge oder sogar beidseitig blind , viele mit Nasenausfluß , manche mit blutenden Verletzungen am Kopf und an den Beinen , einige kolikverdächtig .'}


In [21]:
show_json(PROCESSED_JSONS[1])

In [22]:
len(tree_jsons), len(PROCESSED_JSONS), len(tree_jsons) - len(PROCESSED_JSONS)

(50472, 46265, 4207)

In [1321]:
SKIPPED

Counter({'Meta': 2883,
         'list 2': 26,
         'len 1': 876,
         'list 1': 3,
         'multiple roots (Body)': 171,
         'multiple roots (Header)': 60,
         'error': 72,
         'multiple roots (--)': 116})

In [1322]:
Counter(tiger_json['metadata']['tiger_elem'] for tiger_json in tree_jsons)

Counter({'Header': 4529, 'Body': 40733, 'Meta': 2883, '--': 2327})

In [1329]:
for tiger_json in PROCESSED_JSONS:
    if tiger_json['metadata']['sent_id'] == 's1':
    #if tiger_json['metadata']['text'].startswith('Der Mensch , der '):
        show_json(tiger_json)
        print(tiger_json['metadata'])

{'sent_id': 's1', 'corp_id': 'Tiger2.2', 'text_id': '0001_0001', 'split': 'train', 'tiger_src': 'Frankfurter Rundschau 199207?? ??? ?????????', 'tiger_elem': 'Header', 'text': "`` Ross Perot wäre vielleicht ein prächtiger Diktator ''"}


In [1324]:
! rm -r {OUT_DIR}
! mkdir {OUT_DIR}

In [1325]:
for tree_json in PROCESSED_JSONS:
    tree_id = tree_json['metadata']['sent_id']
    tree_no = int(tree_id[1:])
    if tree_no % 1000 == 0:
        print(tree_no)
    with open(os.path.join(OUT_DIR, f's{tree_no:06}.json'), 'w') as f:
        json.dump(tree_json, f)

1000
2000
3000
4000
5000
6000
7000
8000
9000
10000
11000
12000
13000
14000
15000
16000
17000
18000
19000
20000
21000
22000
23000
24000
25000
26000
28000
29000
30000
31000
32000
33000
34000
35000
36000
37000
38000
39000
40000
41000
42000
43000
44000
45000
46000
47000
48000
49000


In [1326]:
! ls {OUT_DIR} | wc

  46265   46265  601445


In [1327]:
! tar -cJf {OUT_DIR}.tar.xz {OUT_DIR}

In [1328]:
OUT_DIR

'tiger_2.2_UD_headed_JSON'